### Проверка работоспособности и качества пайплайна

Здесь мы еще не запускаем никакое API, а загружаем модель (pipeline) напрямую и проверяем на отложенной (тестовой) выборке

In [1]:
import numpy as np
import pandas as pd
import random

import matplotlib as plt
import matplotlib.image as img
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import train_test_split, cross_val_score

#normalizing data
from sklearn.preprocessing import StandardScaler, MinMaxScaler

#models
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Lasso, Ridge
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
import xgboost as xgb

#metrics
from sklearn.metrics import r2_score as r2, mean_absolute_error as mae, mean_squared_error as mse
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report

from scipy.stats import spearmanr

#model parameters selection
from sklearn.model_selection import KFold, GridSearchCV

#pipeline
from sklearn.pipeline import Pipeline, FeatureUnion
from sklearn.base import BaseEstimator, TransformerMixin

#imputer
from sklearn.impute import SimpleImputer

import pickle
#import dill
import warnings

%matplotlib inline
%config InlineBackend.figure_format = 'svg'

warnings.filterwarnings('ignore')
plt.rcParams.update({'font.size': 14})
pd.set_option('display.max_columns', 500)

In [2]:
TRAIN_DATASET_PATH = './project_data/train.csv'
TEST_DATASET_PATH = './project_data/test.csv'
#MACRO_INFO_PATH = './project_data/macro.csv'
#SAMPLE_SUBMISSION = './project_data/sample_submission.csv'
PREPARED_X_TRAIN_DATASET_PATH = './project_data/X_train.csv'
PREPARED_Y_TRAIN_DATASET_PATH = './project_data/y_train.csv'
PREPARED_X_VALID_DATASET_PATH = './project_data/X_valid.csv'
PREPARED_Y_VALID_DATASET_PATH = './project_data/y_valid.csv'

In [3]:
def evaluate_preds(train_true_values, train_pred_values, test_true_values, test_pred_values):
    """
    Функция выводит основные метрики для оценки модели: R2, MAE, MSE.
    
    """
    print("Train:" + "\n" + 
        "R2:\t" + str(round(r2(train_true_values, train_pred_values), 3)) + "\n" +
        "MAE:\t" + str(round(mae(test_true_values, test_pred_values), 3)) + "\n" +
        "MSE:\t" + str(round(mse(test_true_values, test_pred_values), 3)))
    print("Test:" + "\n" + 
        "R2:\t" + str(round(r2(test_true_values, test_pred_values), 3)) + "\n" +
        "MAE:\t" + str(round(mae(test_true_values, test_pred_values), 3)) + "\n" +
        "MSE:\t" + str(round(mse(test_true_values, test_pred_values), 3)))
    
    plt.figure(figsize=(12,8))
    
    plt.subplot(121)
    sns.scatterplot(x=train_pred_values, y=train_true_values)
    plt.xlabel('Predicted values')
    plt.ylabel('True values')
    plt.title('Train sample prediction')
    
    plt.subplot(122)
    sns.scatterplot(x=test_pred_values, y=test_true_values)
    plt.xlabel('Predicted values')
    plt.ylabel('True values')
    plt.title('Test sample prediction')

    plt.show()

In [4]:
class FeatureSelector(BaseEstimator, TransformerMixin):
    def __init__(self, column):
        self.column = column

    def fit(self, X, y=None):
        return self

    def transform(self, X, y=None):
        return X[self.column]
    
class NumberSelector(BaseEstimator, TransformerMixin):
    """
    Transformer to select a single column from the data frame to perform additional transformations on
    Use on numeric columns in the data
    """
    def __init__(self, key):
        self.key = key

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        return X[[self.key]]
    
class OHEEncoder(BaseEstimator, TransformerMixin):
    def __init__(self, key):
        self.key = key
        self.columns = []

    def fit(self, X, y=None):
        self.columns = [col for col in pd.get_dummies(X, prefix=self.key).columns]
        return self

    def transform(self, X):
        X = pd.get_dummies(X, prefix=self.key)
        test_columns = [col for col in X.columns]
        for col_ in self.columns:
            if col_ not in test_columns:
                X[col_] = 0
        return X[self.columns]
    
class FitMedianNones(BaseEstimator, TransformerMixin):
    def __init__(self, key):
        self.key = key

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X.loc[X[self.key].isnull(), self.key] = X[self.key].median()
        return X[[self.key]]

class FitMedianNonesZeros(BaseEstimator, TransformerMixin):
    def __init__(self, key):
        self.key = key

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        X.loc[(X[self.key] == 0) | (X[self.key].isnull()), self.key] = X[self.key].median()
        return X[[self.key]]

In [5]:
X_train = pd.read_csv(PREPARED_X_TRAIN_DATASET_PATH)
y_train = pd.read_csv(PREPARED_Y_TRAIN_DATASET_PATH)

X_valid = pd.read_csv(PREPARED_X_VALID_DATASET_PATH)
y_valid = pd.read_csv(PREPARED_Y_VALID_DATASET_PATH)

In [6]:
X_valid.tail(3)

full_sq  life_sq  floor  max_floor  material  build_year  num_room  \
7338       53     53.0    1.0        NaN       NaN         NaN       NaN   
7339       32     17.0    6.0       12.0       1.0      1972.0       1.0   
7340       41     21.0    9.0        NaN       NaN         NaN       NaN   

      kitch_sq  metro_km_walk  metro_km_avto  green_zone_km   park_km  \
7338       NaN       5.700245       6.732362       0.183506  6.520123   
7339       6.0       2.129673       1.746509       0.283741  2.465516   
7340       NaN       0.635096       0.635096       0.000000  3.881275   

      water_treatment_km  kremlin_km  full_all  young_all  work_all  \
7338           13.997580   23.373697      7341   0.426100  1.906552   
7339            7.126955   16.470776    112221   0.158883  0.831475   
7340            5.228332   15.891746   1318695   0.016942  0.106304   

      ekder_all  build_count_before_1920  build_count_1921-1945  state  \
7338   0.639559                 0.000000               0.000000    NaN   
7339   0.289803                 0.000000               0.004505    3.0   
7340   0.043290                 0.008834               0.095406    NaN   

      build_count_1946-1970  build_count_1971-1995  build_count_after_1995  \
7338               1.000000               0.000000                0.000000   
7339               0.063063               0.846847                0.085586   
7340               0.358657               0.371025                0.166078   

      raion_build_count_with_builddate_info  green_zone_part  indust_part  \
7338                                    1.0         0.492840     0.075779   
7339                                  222.0         0.153279     0.127376   
7340                                  566.0         0.300284     0.033494   

     oil_chemistry_raion big_market_raion  
7338                  no               no  
7339                  no               no  
7340                  no               no

In [7]:
with open('pipeline_xgb.pkl', 'rb') as in_strm:
    pipeline_xgb = pickle.load(in_strm)

In [8]:
y_train_preds = pipeline_xgb.predict(X_train)
y_valid_preds = pipeline_xgb.predict(X_valid)

In [9]:
evaluate_preds(y_train.values.ravel(), y_train_preds, y_valid.values.ravel(), y_valid_preds)

Train:
R2:	0.665
MAE:	2208052.57
MSE:	14901524736417.008
Test:
R2:	0.428
MAE:	2208052.57
MSE:	14901524736417.008
